# Calcul d'un polygon moyen entre 2 polygones

> Nécessité de calculer un polygone "*moyen*" entre plusieurs polygones

## Première approche: distance minimale et interpolation entre 2 polygones
### Théorie

> *Base*: 2 polygones **A** et **B** avec **B** inclus dans **A**

> *Méthode*: Itération sur chaque paire de polygones pour trouver le polygone moyen (*cf. schéma ci-après*)

> *Libs*: ***Shapely*** avec la méthode ***[interpolate](http://toblerity.org/shapely/manual.html#object.interpolate)***

<img src="moyenne_iso.png" alt="moyenne_iso" width="800"/>

Ceci paraît simple à première vue mais il ne faut pas oublier les difficultés suivantes:
* Les éléments peuvent être des multi polygones (ensemble de polygones)
* Ces polygones/multi polygones peuvent contenir des *trous* (*holes*) qu'il faudra éventuellement prendre en compte:
    * vérifier que chaque paire d'*interior rings* et d'*exterior rings* comprend bien un polygon *within* un autre polygon
    * repérer les polygones les plus grands pour comparer les polygones *majeurs* entre eux et les exclure du calcul par la suite

### Test pratique: Cartes avec des exemples d'isochrones autour de Châtelet
#### Visualisation des différents isochrones
> ***La légende est interactive, pour voir/cacher une couche, il suffit de cliquer dessus dans la légende***

In [1]:
import os

def get_files(path):
    files_list = []
    for root, dirs, files in os.walk(path):  
        for filename in files:
            files_list.append(os.path.join(root,filename))
            
    return files_list

In [2]:
from bokeh.plotting import figure, show
from bokeh.io import output_notebook
from bokeh.tile_providers import STAMEN_TONER_BACKGROUND
from bokeh.models import GeoJSONDataSource
from bokeh.palettes import Viridis
import json

output_notebook()

p = figure()
p.width = 800
p.add_tile(STAMEN_TONER_BACKGROUND, alpha=0.2)

geojsons_path = "./variation_journee"
geojsons = get_files(geojsons_path)
colors = Viridis[len(geojsons)]

for i,geojson in enumerate(geojsons):
    name_legend = geojson.split("\\")[-1].split(".")[0]
    geojson = json.load(open(geojson))
    geo_source = GeoJSONDataSource(geojson=json.dumps(geojson))
    p.patches(
        xs='xs', 
        ys='ys', 
        line_color= colors[i], 
        fill_alpha=0.0, 
        line_alpha=0.8, 
        line_width=2, 
        source=geo_source, 
        legend=name_legend)

p.legend.click_policy="hide"

show(p)

Loading BokehJS ...

#### Calcul du MultiPolygon *moyen*
> On utilise notre propre classe Python importée depuis notre module ***stats_functions***

In [4]:
import sys
import os 
import geopandas as gpd
import itertools
from shapely.geometry import MultiPolygon

add_path = os.getcwd().replace('experiments', '')
sys.path.append(add_path)

import stats_functions as sf

multis = []
ratio_diff = 0.20

for geojson in geojsons:
    gdf = gpd.read_file(geojson)
    multis.append(MultiPolygon(gdf.geometry.values.tolist()))

middle = sf.GetMiddleMultiPoly(multis, ratio_diff).iterate_for_middle()


#### Visualisation cartographique des geojsons et du MultiPolygon *moyen* issu des calculs
> La carte est interactive ainsi que la légende

In [5]:
from geojson import Feature, FeatureCollection, dumps
from shapely.wkt import loads

output_notebook()

p = figure()
p.width = 800
p.add_tile(STAMEN_TONER_BACKGROUND, alpha=0.2)

#Add middle
middle_feature = Feature(geometry=middle)
feature_collection = FeatureCollection([middle_feature])

name_legend = "Middle"
geo_source = GeoJSONDataSource(geojson=dumps(feature_collection))
p.patches(
    xs='xs', 
    ys='ys', 
    fill_color="red",
    line_color="red", 
    fill_alpha=0.05, 
    line_alpha=0.0, 
    line_width=2, 
    source=geo_source, 
    legend=name_legend)

p.legend.click_policy="hide"

#Add others geojsons
geojsons_path = "./variation_journee"
geojsons = get_files(geojsons_path)
colors = Viridis[len(geojsons)]

for i,geojson_ in enumerate(geojsons):
    name_legend = geojson_.split("\\")[-1].split(".")[0]
    geojson_ = json.load(open(geojson_))
    geo_source = GeoJSONDataSource(geojson=json.dumps(geojson_))
    p.patches(
        xs='xs', 
        ys='ys', 
        line_color= colors[i], 
        fill_alpha=0.0, 
        line_alpha=0.8, 
        line_width=2, 
        source=geo_source, 
        legend=name_legend)


show(p)

Loading BokehJS ...

## Seconde approche avec simplification préalable des multipolygones
### Simplifications Shapely/GeoPandas (*voir [ici](http://geopandas.org/geometric_manipulations.html)*) => convex hull, envelope & simplify

> On applique différentes méthodes de simplications avec de calculer le MultiPolygon *moyen*

In [12]:
from bokeh.palettes import Viridis

output_notebook()

#Params
tolerance = 500
ratio_diff = 0.20

#Convex hull
multis_convex = []
for geojson in geojsons:
    gdf = gpd.read_file(geojson).convex_hull
    multis_convex.append(MultiPolygon(gdf.geometry.values.tolist()))

#Envelope
multis_env = []
for geojson in geojsons:
    gdf = gpd.read_file(geojson).envelope
    multis_env.append(MultiPolygon(gdf.geometry.values.tolist()))

#Simplification
multis_simpl = []
for geojson in geojsons:
    gdf = gpd.read_file(geojson).simplify(tolerance, preserve_topology=True)
    multis_simpl.append(MultiPolygon(gdf.geometry.values.tolist()))

simplification={
    "convex":multis_convex,
    "envelope":multis_env,
    "simplify":multis_simpl
}

colors = Viridis[len(simplification)]


#Make the map
p = figure()
p.width = 800
p.add_tile(STAMEN_TONER_BACKGROUND, alpha=0.2)

color=0
for key, value in simplification.items():
    middle = sf.GetMiddleMultiPoly(value, ratio_diff).iterate_for_middle()
    name_legend = key
    #Add middle
    middle_feature = Feature(geometry=middle)
    feature_collection = FeatureCollection([middle_feature])
    geo_source = GeoJSONDataSource(geojson=dumps(feature_collection))

    p.patches(
        xs='xs', 
        ys='ys', 
        fill_color=colors[color],
        line_color=colors[color], 
        fill_alpha=0.05, 
        line_alpha=0.0, 
        line_width=2, 
        source=geo_source, 
        legend=name_legend)

    p.legend.click_policy="hide"
    
    color+=1


show(p)
    

Loading BokehJS ...